Try this Free online SD 1.5 generator with the results: https://perchance.org/fusion-ai-image-generator

 This Notebook is a Stable-diffusion tool which allows you to find similiar prompts to an existing prompt. It uses the Nearest Neighbor decoder method listed here:https://arxiv.org/pdf/2303.03032

In [ ]:
# @title ⚄ Initialize

import os
home_directory = '/content/'
using_Kaggle = os.environ.get('KAGGLE_URL_BASE','')
if using_Kaggle : home_directory = '/kaggle/working/'
%cd {home_directory}

def fix_bad_symbols(txt):
  result = txt
  for symbol in ['^', '}', '{' , ')', '(', '[' , ']' , ':' , '=' ]:
    result = result.replace(symbol,'\\' + symbol)
  #------#
  return result;

def my_mkdirs(folder):
  if os.path.exists(folder)==False:
    os.makedirs(folder)

#🔸🔹
# Load the data if not already loaded
try:
    loaded
except:
  from safetensors.torch import load_file , save_file
  import json , torch , requests , math
  import pandas as pd
  from PIL import Image
  #----#
  %cd {home_directory}
  !git clone https://huggingface.co/datasets/codeShare/fusion-t2i-generator-data
  loaded = True

from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained("openai/clip-vit-large-patch14", clean_up_tokenization_spaces = False)
from transformers import  CLIPProcessor, CLIPModel
processor = CLIPProcessor.from_pretrained("openai/clip-vit-large-patch14" , clean_up_tokenization_spaces = True)
model = CLIPModel.from_pretrained("openai/clip-vit-large-patch14")
logit_scale = model.logit_scale.exp() #logit_scale = 100.00000762939453

%cd {home_directory + 'fusion-t2i-generator-data/'}
!unzip reference.zip
#------#
%cd {home_directory + 'fusion-t2i-generator-data/' + 'reference'}
with open(f'reference_prompts.json', 'r') as f:
  data = json.load(f)
  _df = pd.DataFrame({'count': data})['count']
  target_prompts = {
      key : value for key, value in _df.items()
  }
#------#
with open(f'reference_urls.json', 'r') as f:
  data = json.load(f)
  _df = pd.DataFrame({'count': data})['count']
  target_urls = {
      key : value for key, value in _df.items()
  }

#------#
dot_dtype = torch.float32
dim = 768
reference = torch.zeros(dim).to(dtype = dot_dtype)

Feel free to skip these cells if you do not plan on using them


In [ ]:
# @markdown 🖼️+📝 Choose a pre-encoded reference (optional)
index = 657 # @param {type:"slider", min:0, max:1666, step:1}
PROMPT_INDEX = index
prompt = target_prompts[f'{PROMPT_INDEX}']
url = target_urls[f'{PROMPT_INDEX}']
if url.find('perchance')>-1:
  image = Image.open(requests.get(url, stream=True).raw)
#------#
try: reference
except: reference = torch.zeros(dim).to(dtype = dot_dtype)
if reference == '': reference = torch.zeros(dim).to(dtype = dot_dtype)
# @markdown ⚖️ 🖼️ encoding <-----?-----> 📝 encoding </div> <br>
C = 0.3 # @param {type:"slider", min:0, max:1, step:0.01}
log_strength = 1 # @param {type:"slider", min:-5, max:5, step:0.01}
%cd {home_directory + 'fusion-t2i-generator-data/' + 'reference'}
references = torch.load('reference_text_and_image_encodings.pt'  , weights_only=False)
reference = torch.add(reference, math.pow(10 ,log_strength-1) * C * references[index][0].dequantize().to(dtype = torch.float32))
reference = torch.add(reference, math.pow(10 ,log_strength-1) * (1-C) * references[index][1].dequantize().to(dtype = torch.float32))
references = '' # Clear up memory
ref = reference.clone().detach()
#------#
print(f'Prompt for this image : \n\n "{prompt} " \n\n')
image

In [ ]:
# @markdown 🖼️ Upload your own image for use as reference via URL (optional)
URL = '' # @param {type:'string' ,placeholder:'paste an url here'}
image = Image.open(requests.get(URL, stream=True).raw)
#---------#
# Get image features
inputs = processor(images=image, return_tensors="pt")
image_features = model.get_image_features(**inputs)
image_features = image_features / image_features.norm(p=2, dim=-1, keepdim=True)
#-----#
log_strength = 1 # @param {type:"slider", min:-5, max:5, step:0.01}
ref = ref + math.pow(10,log_strength-1)*image_features
image

In [ ]:
# @markdown 🖼️ Upload your own image in the /content/ folder for use as reference (optional)
FILENAME = '' # @param {type:'string' ,placeholder:'IMG_123.png'}
import cv2
image = cv2.imread(FILENAME)
image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)

#---------#
# Get image features
inputs = processor(images=image, return_tensors="pt")
image_features = model.get_image_features(**inputs)
image_features = image_features / image_features.norm(p=2, dim=-1, keepdim=True)
#-----#
log_strength = 1 # @param {type:"slider", min:-5, max:5, step:0.01}
ref = ref + math.pow(10,log_strength-1)*image_features
image

Save the reference prior to running the Interrogator

In [ ]:
# @title ⚄ Save the reference
try: ref
except: ref = torch.zeros(dim)
_ref = {}
_ref['weights'] = ref.to(dot_dtype)
%cd /content/
save_file(_ref , 'reference.safetensors' )

In [ ]:
# @title ⚄ Run the CLIP interrogator on the saved reference
LIST_SIZE = 1000  # @param {type:'number' , placeholder:'set how large the list should be'}
START_AT = 0  # @param {type:'number' , placeholder:'set how large the list should be'}
# @markdown -----
# @markdown Select vocab
general = False # @param {type:"boolean"}
civit9 = True # @param {type:"boolean"}
fanfic1 = False # @param {type:"boolean"}
fanfic2 = False # @param {type:"boolean"}
# @markdown -----
# @title ⚄ New interrogator code using quantized text corpus
%cd /content/
_ref = load_file('reference.safetensors' )
ref = _ref['weights'].to(dot_dtype)
# @markdown 📝 Enhance/Penalize Similarity and skip items containing word(s)
POS1 = '' # @param {type:'string' ,placeholder:'item1 , item2 , ...'}
POS2 = '' # @param {type:'string' ,placeholder:'item1 , item2 , ...'}
NEG = ''# @param {type:'string' ,placeholder:'item1 , item2 , ...'}
SKIP = '' # @param {type:'string' ,placeholder:'item1 , item2 , ...'}
min_wordcount = 0 # @param {type:"slider", min:0, max:20, step:1}
def isBlacklisted(_txt):
  blacklist =  SKIP.lower().replace('</w>' , ' ').replace('{' , '').replace('}' , '').replace('|' , ',').strip()
  if blacklist == '': return False
  txt = _txt.lower().strip()
  if len(txt)<min_wordcount: return True
  if txt.isnumeric(): return True
  #-----#
  for item in list(blacklist.split(',')):
    if item.strip() == '' : continue
    if txt.find(item.strip())> -1 : return True
  #------#
  found = False
  alphabet = 'abcdefghijklmnopqrstuvxyz'
  for letter in alphabet:
    found =  txt.find(letter)>-1
    if found:break
  #------#
  return not found
# @markdown -----
# @markdown logarithmic prompt strength x for value 10^(x-1)
_POS1 = 1 # @param {type:"slider", min:-5, max:5, step:0.01}
_POS2 = 1 # @param {type:"slider", min:-5, max:5, step:0.01}
_NEG = 1 # @param {type:"slider", min:-5, max:5, step:0.01}
# @markdown -----
for _item in POS1.split(','):
  item = _item.strip()
  if item == '':continue
  inputs = tokenizer(text = item.strip(), truncation = True  , padding=True, return_tensors="pt")
  ref = ref + math.pow(10,_POS1-1) * model.get_text_features(**inputs)[0]
#-------#
for _item in POS2.split(','):
  item = _item.strip()
  if item == '':continue
  inputs = tokenizer(text = item.strip(), truncation = True  , padding=True, return_tensors="pt")
  ref = ref + math.pow(10,_POS2-1) * model.get_text_features(**inputs)[0]
#-------#
for _item in NEG.split(','):
  item = _item.strip()
  if item == '':continue
  inputs = tokenizer(text = item.strip(), truncation = True  , padding=True, return_tensors="pt")
  ref = ref + math.pow(10,_NEG-1) * model.get_text_features(**inputs)[0]
#------#
ref = (ref/ref.norm(p=2, dim=-1, keepdim=True)).to(dtype = dot_dtype)
vocab_to_load = ''
if (general): vocab_to_load = vocab_to_load + 'general , '
if (civit9): vocab_to_load = vocab_to_load + 'civit9 , '
if (fanfic1): vocab_to_load = vocab_to_load + 'fanfic1 , '
if (fanfic2): vocab_to_load = vocab_to_load + 'fanfic2 , '
vocab_to_load = (vocab_to_load +'}').replace(' , }' , '')
multi = vocab_to_load.find(',')>-1

#-----#
prompts_folder = f'{home_directory}fusion-t2i-generator-data/vocab-v2/text'
encodings_folder = f'{home_directory}fusion-t2i-generator-data/vocab-v2/text_encodings'
#----#
scale = 0.0043
size = 0
#------#
total_items = 0
for filename in os.listdir(prompts_folder):
  if (not general and filename.find('general')>-1):continue
  if (not civit9 and filename.find('civit9')>-1):continue
  if (not fanfic1 and filename.find('fanfic1')>-1):continue
  if (not fanfic2 and filename.find('fanfic2')>-1):continue
  size = size + LIST_SIZE
#-------#
similiar_sims = torch.zeros(size)
similiar_prompts = {}
_index = 0
#-------#
similiar_encodings = {}
for filename in os.listdir(prompts_folder):
  if (not general and filename.find('general')>-1):continue
  if (not civit9 and filename.find('civit9')>-1):continue
  if (not fanfic1 and filename.find('fanfic1')>-1):continue
  if (not fanfic2 and filename.find('fanfic2')>-1):continue
  #------#
  root_filename = filename.replace('.json', '')
  %cd {prompts_folder}
  prompts = {}
  with open(f'{root_filename}.json', 'r') as f:
    data = json.load(f).items()
    for key,value in data:
      prompts[key] = value
  num_items = int(prompts['num_items'])
  total_items = total_items + num_items

  #------#
  try:vocab_loaded
  except:
    vocab_loaded = 'first'
  #-----#

  if  vocab_loaded == 'first' or (vocab_loaded != vocab_to_load and not multi):
    %cd {encodings_folder}
    _text_encodings = load_file(f'{root_filename}.safetensors')['weights'].to(torch.uint8)
    text_encodings = torch.zeros(num_items , dim)
    tmp = torch.ones(dim).to(dot_dtype)
    for index in range(num_items):
      text_encodings[index] = torch.sub(_text_encodings[index][1:dim+1].to(dot_dtype) , tmp , alpha= _text_encodings[index][0].to(dot_dtype))
    vocab_loaded = vocab_to_load
  #------#


  sims = torch.matmul(text_encodings*scale, ref.t())
  sorted , indices = torch.sort(sims , dim=0 , descending = True)
  #-----#
  for index in range(LIST_SIZE + START_AT):
    if index<START_AT: continue
    key = indices[index].item()
    try:prompt = prompts[f'{key}']
    except:continue
    if(isBlacklisted(prompt)):continue
    #-------#
    similiar_sims[_index] = torch.tensor(round(sims[key].item(), 5))
    similiar_prompts[f'{_index}'] = prompt
    _index = _index + 1
  #-------#
  continue
#---------#
print(f'\n\nProcessed entire list of {total_items} items to find closest match. Saved closest matching indices {START_AT} to {START_AT + LIST_SIZE} as the dict "similiar_prompts" with {LIST SIZE} items. \n\n')


In [ ]:

# @title ⚄ Printing results from text corpus
sorted , indices = torch.sort(similiar_sims , dim=0 , descending = True)
include_similiarity = False # @param {type:"boolean"}
print_as_list = False # @param {type:"boolean"}
N = 7 # @param {type:"slider", min:0, max:10, step:1}

if(print_as_list):
  for index in range(LIST_SIZE):
    key = indices[index].item()
    sim = similiar_sims[key].item()
    prompt = similiar_prompts[f'{key}']
    if include_similiarity :print(f'{prompt}  - {round(sim*100,1)} %')
    else: print(f'{prompt}')
#-------#
else:
  prompt = ''
  for iter in range(N):
    prompt = prompt + '{'
    for index in range(LIST_SIZE):
      key = indices[index].item()
      sim = similiar_sims[key].item()
      prompt = prompt + fix_bad_symbols(similiar_prompts[f'{key}']) + '|'
    #-----#
    prompt = (prompt + '}').replace('|}',  '} ')
  #------#
  print(f'\ Similiar prompts: \n\n {prompt} \n\n')
  image
#-----#


OTHER STUFF BELOW - Code for the modules below are work-in-progress.

The savefile can be used here : https://perchance.org/fusion-ai-image-generator

In [ ]:
# @title 	⚄ Create fusion-generator .json savefile from result
filename = 'blank.json'
path = '/content/text-to-image-prompts/fusion/'

print(f'reading {filename}....')
_index = 0
%cd {path}
with open(f'{filename}', 'r') as f:
  data = json.load(f)
#------#
_df = pd.DataFrame({'count': data})['count']
_savefile = {
    key : value for key, value in _df.items()
}
#------#
from safetensors.torch import load_file
import json , os , torch
import pandas as pd
#----#
def my_mkdirs(folder):
  if os.path.exists(folder)==False:
    os.makedirs(folder)
#------#
savefile_prompt = ''
for i in range(N) : savefile_prompt = savefile_prompt + ' ' + __prompts
_savefile['main'] = savefile_prompt.replace('\n', ' ').replace('  ', ' ').replace('   ', ' ')
#------#
save_filename = f'fusion_C05_X7_1000_{PROMPT_INDEX}.json'
output_folder = '/content/output/savefiles/'
my_mkdirs(output_folder)
#-----#
%cd {output_folder}
print(f'Saving segment {save_filename} to {output_folder}...')
with open(save_filename, 'w') as f:
    json.dump(_savefile, f)


In [ ]:
# @title 	⚄ Create a savefile-set from the entire range of pre-encoded items

# @markdown 📥 Load the data (only required one time)
load_the_data = True # @param {type:"boolean"}

import math
from safetensors.torch import load_file
import json , os , torch
import pandas as pd
from PIL import Image
import requests

def my_mkdirs(folder):
  if os.path.exists(folder)==False:
    os.makedirs(folder)

# @markdown ⚖️ Set the value for C in the reference  <br> <br> sim = C* text_enc + image_enc*(1-C) <br><br>

C = 0.5 # @param {type:"slider", min:0, max:1, step:0.01}

# @markdown 🚫 Penalize similarity to this prompt(optional)
if(load_the_data):
  target_prompts , target_text_encodings , urls , target_image_encodings , NUM_ITEMS =  getPromptsAndLinks('/content/text-to-image-prompts/fusion')
  from transformers import AutoTokenizer
  tokenizer = AutoTokenizer.from_pretrained("openai/clip-vit-large-patch14", clean_up_tokenization_spaces = False)
  from transformers import  CLIPProcessor, CLIPModel
  processor = CLIPProcessor.from_pretrained("openai/clip-vit-large-patch14" , clean_up_tokenization_spaces = True)
  model = CLIPModel.from_pretrained("openai/clip-vit-large-patch14")
  logit_scale = model.logit_scale.exp() #logit_scale = 100.00000762939453
#---------#

filename = 'blank.json'
path = '/content/text-to-image-prompts/fusion/'
print(f'reading {filename}....')
_index = 0
%cd {path}
with open(f'{filename}', 'r') as f:
  data = json.load(f)
#------#
_df = pd.DataFrame({'count': data})['count']
_blank = {
    key : value for key, value in _df.items()
}
#------#

root_savefile_name = 'fusion_C05_X7'

%cd /content/
output_folder = '/content/output/savefiles/'
my_mkdirs(output_folder)
my_mkdirs('/content/output2/savefiles/')
my_mkdirs('/content/output3/savefiles/')
my_mkdirs('/content/output4/savefiles/')
my_mkdirs('/content/output5/savefiles/')
my_mkdirs('/content/output6/savefiles/')
my_mkdirs('/content/output7/savefiles/')
my_mkdirs('/content/output8/savefiles/')
my_mkdirs('/content/output9/savefiles/')
my_mkdirs('/content/output10/savefiles/')
my_mkdirs('/content/output11/savefiles/')
my_mkdirs('/content/output12/savefiles/')
my_mkdirs('/content/output13/savefiles/')


NEG = '' # @param {type:'string'}
strength = 1 # @param {type:"slider", min:-5, max:5, step:0.1}

for index in range(1667):

  PROMPT_INDEX = index
  prompt = target_prompts[f'{index}']
  url = urls[f'{index}']
  if url.find('perchance')>-1:
    image = Image.open(requests.get(url, stream=True).raw)
  else: continue #print("(No image for this ID)")

  print(f"no. {PROMPT_INDEX} : '{prompt}'")
  text_features_A = target_text_encodings[f'{index}']
  image_features_A =  target_image_encodings[f'{index}']
  # text-similarity
  sims =  C * torch.matmul(text_tensor, text_features_A.t())

  neg_sims = 0*sims
  if(NEG != ''):
    # Get text features for user input
    inputs = tokenizer(text = NEG, padding=True, return_tensors="pt")
    text_features_NEG = model.get_text_features(**inputs)
    text_features_NEG = text_features_A/text_features_A.norm(p=2, dim=-1, keepdim=True)
    # text-similarity
    neg_sims =  strength*torch.matmul(text_tensor, text_features_NEG.t())
  #------#

  # plus image-similarity
  sims = sims +  (1-C) * torch.matmul(text_tensor, image_features_A.t()) * logit_scale

  # minus NEG-similarity
  sims = sims - neg_sims

  # Sort the items
  sorted , indices = torch.sort(sims,dim=0 , descending=True)

  # @markdown Repeat output N times
  RANGE = 1000
  NUM_CHUNKS = 10+
  separator = '|'
  _savefiles = {}
  #-----#
  for chunk in range(NUM_CHUNKS):
    if chunk=<10:continue
    start_at_index = chunk * RANGE
    _prompts = ''
    for _index in range(start_at_index + RANGE):
      if _index < start_at_index : continue
      index = indices[_index].item()
      prompt = prompts[f'{index}']
      _prompts = _prompts.replace(prompt + separator,'')
      _prompts = _prompts  + prompt + separator
    #------#
    _prompts = fix_bad_symbols(_prompts)
    _prompts = ('{' + _prompts + '}').replace(separator + '}', '}')
    _savefiles[f'{chunk}'] = _prompts
  #---------#
  save_filename = f'{root_savefile_name}_{start_at_index + RANGE}_{PROMPT_INDEX}.json'


  if (chunk=<20 && chunk>10): %cd '/content/output2/savefiles/'
  if (chunk<=30 && chunk>20): %cd '/content/output3/savefiles/'
  if (chunk=<40 && chunk>30): %cd '/content/output4/savefiles/'
  if (chunk<=50 && chunk>40): %cd '/content/output5/savefiles/'
  if (chunk=<60 && chunk>50): %cd '/content/output6/savefiles/'
  if (chunk<=70 && chunk>60): %cd '/content/output7/savefiles/'
  if (chunk=<80 && chunk>70): %cd '/content/output8/savefiles/'
  if (chunk<=90 && chunk>80): %cd '/content/output9/savefiles/'
  if (chunk=<100 && chunk>90): %cd '/content/output10/savefiles/'
  if (chunk<=110 && chunk>100): %cd '/content/output11/savefiles/'
  if (chunk=<120 && chunk>110): %cd '/content/output12/savefiles/'
  if (chunk<=130 && chunk>120): %cd '/content/output13/savefiles/'


  #------#
  print(f'Saving savefile {save_filename} to {output_folder}...')
  with open(save_filename, 'w') as f:
      json.dump(_savefiles, f)
  #---------#
  continue
#-----------#

In [ ]:
# Determine if this notebook is running on Colab or Kaggle
#Use https://www.kaggle.com/ if Google Colab GPU is busy
home_directory = '/content/'
using_Kaggle = os.environ.get('KAGGLE_URL_BASE','')
if using_Kaggle : home_directory = '/kaggle/working/'
%cd {home_directory}
#-------#

# @title Download the text_encodings as .zip
import os
%cd {home_directory}
#os.remove(f'{home_directory}results.zip')
root_output_folder = home_directory + 'output/'
zip_dest = f'/content/results.zip' #drive/MyDrive
!zip -r {zip_dest} {root_output_folder}

In [ ]:
# @title 	⚄ Quick fix for normalizing encoded text corpus tensors

import os
my_mkdirs('/content/output')
my_mkdirs('/content/output/text_encodings')

for filename in os.listdir(f'{prompts_folder}'):
  %cd {prompts_folder}
  prompts = {}
  with open(f'{filename}', 'r') as f:
    data = json.load(f).items()
    for key,value in data:
      prompts[key] = value
    #------#
  num_items = int(prompts['num_items'])

  %cd {encodings_folder}
  enc_filename = filename.replace('json', 'safetensors')
  _text_encodings = load_file(f'{enc_filename}')['weights'].to(torch.uint8)
  text_encodings = torch.zeros(num_items , dim)
  tmp = torch.ones(dim)
  tmp2 = torch.tensor(1/0.0043)
  zero_point = 0
  for index in range(num_items):
    text_encodings[index] = torch.tensor(0.0043) * torch.sub(_text_encodings[index][1:dim+1] , tmp , alpha= _text_encodings[index][0]).to(torch.float32)
    text_encodings[index] = tmp2*text_encodings[index]/text_encodings[index].norm(p=2, dim=-1, keepdim = True)
    test = torch.round( torch.add(text_encodings[index],tmp*zero_point))
    less_than_zero = test<0
    while(torch.any(less_than_zero).item()):
      zero_point = zero_point + 1
      test = torch.round( torch.add(text_encodings[index],tmp*zero_point))
      less_than_zero = test<0
    #------#
    _text_encodings[index][0]  = zero_point
    _text_encodings[index][1:dim+1] = test
  #-------#
  %cd /content/output/text_encodings

  tmp = {}
  tmp['weights'] =  _text_encodings.to(torch.uint8)
  tmp['num_items'] = torch.tensor(num_items).to(torch.uint8)
  tmp['scale'] = torch.tensor(0.0043)
  save_file(tmp , f'{enc_filename}')
#------#

In [ ]:
# Check the average value for this set
sims = torch.matmul(vocab_encodings.dequantize(),average.t())
sorted , indices = torch.sort(sims,dim=0 , descending=True)
for index in range(10):
  print(prompts[f'{indices[index].item()}'])